<a href="https://colab.research.google.com/github/kimjc95/computational-chemistry/blob/main/Protein_MD_in_Colab_(KOR).ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# MD simulation을 Google Colab에서
2024-07-28 by Joo-Chan Kim at MSBL, KAIST

단백질, DNA, RNA 등의 분자동역학 시뮬레이션을 위한 구글 코랩 노트북입니다.
배포, 수정, 상업적 이용은 저작자 표기 조건 하에서 자유입니다. (BSD-3)

인용 시에는 DOI:[10.5281/zenodo.13133762](https://doi.org/10.5281/zenodo.13133762)를 사용해주세요.

사용 시 문제가 있다면 제 [깃헙](https://github.com/kimjc95/computational-chemistry/issues)이나 이메일(kimjoochan@kaist.ac.kr)로 알려주세요.

-------------------------------------

**준비물 : **

1. 단백질/DNA/RNA의 PDB 파일 혹은 4자리 PDB ID

2. 구글 계정 (구글 코랩 및 구글 드라이브), 인터넷 연결

In [ ]:
#@markdown GPU 런타임 여부를 확인하기 위해 이 셀을 실행해주세요.
import torch
if not torch.cuda.is_available():
    print("GPU 런타임이 아닙니다. 런타임 - 런타임 유형 변경에서 GPU를 선택해주세요.")
    print("MD 계산은 GPU 가속 없이는 매우 느립니다.")
else:
    print("GPU 감지됨!")

GPU 감지됨!


In [ ]:
#@markdown conda 환경 설치를 위해 이 셀을 실행해주세요. 런타임이 끊겼다가 다시 연결됩니다.
!pip install -q condacolab
import condacolab
condacolab.install()

⏬ Downloading https://github.com/conda-forge/miniforge/releases/download/23.11.0-0/Mambaforge-23.11.0-0-Linux-x86_64.sh...
📦 Installing...
📌 Adjusting configuration...
🩹 Patching environment...
⏲ Done in 0:00:13
🔁 Restarting kernel...


In [ ]:
#@title #0. 필요 패키지 설치 및 Google Drive 연결
#@markdown (2분 가량 소요) 구글 드라이브 연결을 묻는 메시지가 뜨면 승인해주세요.
#@markdown 구글 코랩 세션이 끊기더라도 다시 이어갈 수 있게 하기 위함입니다.

import subprocess

print("필수 패키지 설치중...", end='')
subprocess.run("mamba install -c conda-forge numpy scikit-learn openmm pdbfixer mdtraj nglview plotly ipywidgets=7", shell=True)
subprocess.run("pip install pdb2pqr", shell=True)
print("완료.")

from time import sleep
from pdbfixer import PDBFixer
import locale
import warnings
import threading
import numpy as np
from openmm import *
from openmm.app import *
from openmm.unit import *
from tqdm import tqdm_notebook
import os
import mdtraj as md
import nglview as nv
from sklearn.cluster import AgglomerativeClustering
from sklearn.decomposition import PCA
from collections import Counter
import plotly.graph_objects as go
import plotly.io as pio
from plotly.subplots import make_subplots
pio.renderers.default = "colab"
from google.colab import output, files, drive
output.enable_custom_widget_manager()
warnings.filterwarnings("ignore")
drive.flush_and_unmount()
drive.mount('/content/drive', force_remount=True)

필수 패키지 설치중...완료.


Drive not mounted, so nothing to flush and unmount.
Mounted at /content/drive


In [ ]:
#@title #1. 작업 폴더 지정
#@markdown 구글 드라이브 안에 위치할 작업 폴더명을 입력해주세요..

#@markdown 해당 이름을 갖는 폴더가 없으면 새로 생성됩니다.

save_directory = "test" #@param {type:"string"}

save_at = "/content/drive/MyDrive/"+save_directory

if os.path.isdir(save_at):
    print("이미 "+save_directory+"란 이름의 폴더가 구글 드라이브에 존재합니다.")
    if os.path.exists(save_at+"/MD_processed.xtc"):
        print("분석 완료된 MD trajectory 파일이 존재합니다.")
        print("다른 폴더 이름을 지정하세요.")

    elif os.path.exists(save_at+"/settings.txt"):
        print("현재 MD 시뮬레이션 설정 값들은 다음과 같습니다.")
        with open(save_at+"/settings.txt", 'r') as f:
            for line in f.readlines():
                print(line, end='')
        print("\n설정 변경을 원하시면 3. MD 조건 설정 셀을 실행하세요.")
        print("계산을 이어하시려면 4. 시뮬레이션 준비 셀을 실행하세요.")

    elif os.path.exists(save_at+"/protein.pdb"):
        print("protein.pdb 파일이 존재합니다.")
        print("3. MD 조건 설정 셀을 실행하세요.")

    else:
        print(save_directory+"란 이름의 폴더가 존재하지만, 비어있습니다.")
        print("2. Input 파일 준비 셀부터 순서대로 진행하세요.")

else:
    subprocess.run("mkdir "+save_at, shell=True)
    print(save_directory+"라는 이름의 새 폴더가 구글 드라이브 내에 생성되었습니다.")

save_at += '/'

test라는 이름의 새 폴더가 구글 드라이브 내에 생성되었습니다.


In [ ]:
#@title #2. Input 파일 준비
#@markdown 4자리 PDB ID를 입력하세요. 빈칸으로 남기면 원하는 PDB 파일을 업로드 할 수 있습니다.

PDB_ID = "3nir" # @param {type:"string"}
##@markdown For non-standard residues that are defined in [RCSB Chemical Component Dictionary](https://www.wwpdb.org/data/ccd),
##@markdown type the 3-letter residue name below. For more than one non-standard residues, separate them using commas.
#non_standard_residues = "SEC" # @param {type:"string"}
#@markdown 리간드 등의 heterogen을 제거하고 싶다면 아래 박스를 체크해주세요.
remove_Heterogens = False # @param {type:"boolean"}

if PDB_ID == "":
    pdbfile = files.upload()
    fixer = PDBFixer(filename=next(iter(pdbfile)))
else:
    fixer = PDBFixer(pdbid=PDB_ID)

"""
if non_standard_residues != "":
    ncAAs = non_standard_residues.split(',')
    for ncaa in ncAAs:
        fixer.downloadTemplate(ncaa)
"""
print("PDB 파일을 고치고 있습니다...", end='')
fixer.findMissingResidues()
fixer.removeHeterogens(remove_Heterogens)
fixer.findMissingAtoms()
fixer.addMissingAtoms()
print("완료.")
#fixer.addMissingHydrogens(pH)

with open(save_at+"protein.pdb", 'w') as f:
    PDBFile.writeFile(fixer.topology, fixer.positions, f)

output.enable_custom_widget_manager()
view1 = nv.NGLWidget()
view1._set_size('750px','500px')
view1.add_structure(nv.FileStructure(save_at+"protein.pdb"))
view1.add_representation("cartoon")
view1.add_licorice("protein or nucleic")
view1

PDB 파일을 고치고 있습니다...완료.


NGLWidget()

In [ ]:
#@title #3. MD 조건 설정
#@markdown 아래 조건들을 잘 설정한뒤 셀을 실행해주세요. 실행 결과를 잘 확인후 다음 셀로 진행해주세요.

#@markdown ForceField를 설정해주세요.
forcefield = "Amber14" #@param ["Amber14", "CHARMM36", "AMOEBA 2018"]
#@markdown 물 분자모델을 설정해주세요. (explicit)의 경우 물 분자들이 추가됩니다.
waterModel = "(explicit) TIP3P" #@param ["(explicit) TIP3P", "(explicit) SPC/E", "(explicit) TIP4P-Ew", "(explicit) TIP5P", "(explicit) OPC", "(explicit) OPC3", "(implicit) HCT (igb=1)", "(implicit) OBC1 (igb=2)", "(implicit) OBC2 (igb=5)", "(implicit) GBn (igb=7)", "(implicit) GBn2 (igb=8)"]
#@markdown 수소 원자를 붙이기 위한 기준 pH를 설정해주세요.
pH = 7.4 # @param {type:"slider", min:0.0, max:14.0, step:0.1}
#@markdown 용액의 이온 세기 (몰 농도)를 정해주세요.
ion_conc = 0.15 #@param {type:"slider", min:0.0, max:2.0, step:0.05}
#@markdown (explicit) 용매 모델의 경우 추가되는 물층의 두께 (nm)를 입력해주세요.
padding = 1.5 #@param {type:"slider", min:1.0, max:5.0, step:0.1}
#@markdown 추가되는 양이온의 종류를 입력해주세요.
cation = "Na+" #@param ["Li+", "Na+", "K+", "Rb+", "Cs+"]
#@markdown 추가되는 음이온의 종류를 입력해주세요.
anion = "Cl-" #@param ["F-", "Cl-", "Br-", "I-"]
#@markdown 용매 물 분자들의 진동을 생략하면 step_size를 키워 계산을 더 빨리 할 수 있습니다.
rigidWater = True #@param {type:"boolean"}
#@markdown 조화진동자 계산을 추가로 생략 가능합니다. None : 고정 없음, HBonds : 수소를 포함하는 결합 길이 고정, AllBonds : 모든 결합의 길이 고정, HAngles : 수소를 포함하는 결합각 고정
constraints = "HBonds" #@param ["None", "HBonds", "AllBonds", "HAngles"]
#@markdown 수소 원자의 질량을 키워서 진동수를 감소시키면 step_size를 키워 계산을 더 빨리할 수 있습니다. (단위 : amu)
hydrogenMass = 2 #@param {type:"slider", min:1.0, max:4.0, step:0.1}
#@markdown 계산의 정밀도를 설정하세요. (빠름) single -> mixed -> double (느림)
precision = "single" #@param ["single", "mixed", "double"]
#@markdown 몇 fs마다 원자들의 위치를 계산할지 정하세요.
step_size = 2.5 #@param {type:"slider", min:0.1, max:4, step:0.1}
#@markdown 계산할 계의 **섭씨 온도**를 정하세요.
temperature = 25 #@param {type:"slider", min:0.0, max:100.0, step:1.0}
#@markdown 계산할 계의 압력 (bar)을 정하세요.
pressure = 1.0 #@param {type:"slider", min:0.0, max:100.0, step:1.0}
#@markdown 본격적인 계산에 앞서 설정한 온도/압력과 계가 평형을 이룰 시간을 몇 ps나 줄지 정하세요.
eq_time = 100 #@param {type:"slider", min:0.0, max:1000.0, step:10.0}
#@markdown 분석용 계산을 몇 ns 돌릴 것인지 정하세요.
run_time = 1 #@param {type:"slider", min:1, max:500.0, step:1}
#@markdown 몇 ps마다 원자들의 위치를 기록할 것인지 정하세요.
save_interval = 10 #@param {type:"slider", min:1, max:50, step:1}
#@markdown 구글 코랩이 끊어지는 일을 대비해서 몇 분 (실제 시간)마다 백업할지 정하세요.
backup_interval = 15 #@param {type:"slider", min:5, max:60, step:5}


if forcefield == "Amber14" and waterModel == "(explicit) TIP5P":
    print("경고 : AMBER forcefield는 TIP5P 모델을 지원하지 않습니다.")
    print("다른 보기를 골라주세요.")

elif forcefield == "CHARMM36" and waterModel.startswith("(explicit) OPC"):
    print("경고 : CHARMM forcefield는 OPC 모델을 지원하지 않습니다.")
    print("다른 보기를 골라주세요.")

elif forcefield == "CHARMM36" and padding < 1.2:
    print("경고 : CHARMM forcefield에선 PBC 상자 크기가 더 커야 합니다.")
    print("padding 변수를 더 키워주세요.")

else:
    if forcefield == "AMOEBA 2018":
        print("주의 : AMOEBA forcefield에서는 결합을 고정할 수 없습니다. 선택된 contraints, rigidWater 옵션이 무의미합니다.")
        if waterModel.startswith("(explicit)"):
            print("주의 : AMOEBA forcefield에서는 물 분자 모델이 하나 뿐이라 선택된 waterModel 옵션은 무의미합니다.")
        if hydrogenMass == 1.0 and step_size > 0.5:
            print(f"주의 : 고정된 결합이 없어 {step_size} fs의 step_size로 계산을 돌렸다간 시뮬레이션이 터질 수 있습니다.")
        elif hydrogenMass < 2.0 and step_size > 2.0:
            print(f"주의 : 수소 질량이 {hydrogenMass} amu지만 여전히 step_size가 너무 큰 것 같습니다. 시뮬레이션이 터질 수도 있습니다.")

    if waterModel.startswith("(implicit)"):
        print("주의 : Implicit 용매 조건을 고르셨습니다. 이 경우 padding, cation, anion, rigidWater, pressure 옵션이 무의미합니다.")

    if hydrogenMass == 1.0 and not rigidWater and constraints == 'None' and step_size > 0.5:
        print(f'주의 : 고정된 결합이 없습니다. {step_size} fs의 step_size로는 시뮬레이션이 터질 수 있습니다.')

    elif hydrogenMass == 1.0 and constraints == 'HBonds' and step_size > 2.0:
        print(f'주의 : step_size가 너무 큰 것 같습니다. 시뮬레이션이 터질 수도 있습니다.')

    # Setting the input parameters for PDB2PQR
    if waterModel.startswith("(explicit)"):
        if forcefield == 'Amber14':
            ffin = "AMBER"
        elif forcefield == 'CHARMM36':
            ffin = "CHARMM"
        else:
            ffin = "PARSE"
    else:
        ffin = "PARSE"

    # For implicit solvent systems, PARSE forcefield is recommended
    # For the compatibility with Modeller, set --ffout as AMBER
    params = f' --ff {ffin} --ffout AMBER --pdb-output {save_at}protein_with_H.pdb'
    params += f' --titration-state-method propka --with-ph {pH} --pH {pH} --drop-water'
    params += f' {save_at}protein.pdb protein_with_H.pqr'

    print("PDB2PQR로 protein.pdb에 수소 원자를 더하는중...", end='')
    subprocess.run("pdb2pqr"+params, shell=True)

    if not os.path.exists(save_at+"protein_with_H.pdb"):
        print("실패.")
        print("PDBFixer로 시도하는 중...", end='')
        fixer = PDBFixer(filename=save_at+"protein.pdb")
        fixer.addMissingHydrogens(pH)
        with open(save_at+"protein_with_H.pdb", 'w') as f:
            PDBFile.writeFile(fixer.topology, fixer.positions, f)

    print("완료.")

    view2 = nv.NGLWidget()
    view2._set_size('750px','500px')
    view2.add_structure(nv.FileStructure(save_at+"protein_with_H.pdb"))
    view2.add_representation("cartoon")
    view2.add_licorice("protein or nucleic")
    display(view2)

    with open(save_at+"settings.txt", 'w') as f:
        f.write("forcefield : "+forcefield)
        f.write("\nconstraints : "+constraints)
        f.write("\npadding : "+str(padding))
        f.write("\nion_conc : "+str(ion_conc))
        f.write("\ncation : "+cation)
        f.write("\nanion : "+anion)
        f.write("\nhydrogenMass : "+str(hydrogenMass))
        f.write("\nwaterModel : "+waterModel)
        f.write("\nrigidWater : "+str(rigidWater))
        f.write("\nstep_size : "+str(step_size))
        f.write("\ntemperature : "+str(temperature))
        f.write("\npressure : "+str(pressure))
        f.write("\neq_time : "+str(eq_time))
        f.write("\nrun_time : "+str(run_time))
        f.write("\nsave_interval : "+str(save_interval))
        f.write("\nbackup_interval : "+str(backup_interval))
        f.write("\nprecision : "+precision)
    print("설정 값이 settings.txt에 저장되었습니다.")
    print("이제 밑에 있는 4. 시뮬레이션 준비 셀을 실행하세요.")

protein.pdb에 수소 원자를 더하는중...완료.


NGLWidget()

설정 값이 settings.txt에 저장되었습니다.
이제 밑에 있는 4. 시뮬레이션 준비 셀을 실행하세요.


In [ ]:
#@title #4. 시뮬레이션 준비

def read_settings(save_at):
    """
    Reads the parameter values from the setting.txt file.
    Returns the settings dictionary.
    """
    if not os.path.exists(save_at+"settings.txt"):
        return None

    with open(save_at+"settings.txt", 'r') as f:
        for line in f.readlines():
            if line.startswith("forcefield"):
                forcefield = line.split(":")[1].strip()
            elif line.startswith("constraints"):
                constraints = line.split(":")[1].strip()
            elif line.startswith("padding"):
                padding = float(line.split(":")[1].strip())*nanometers
            elif line.startswith("ion_conc"):
                ion_conc = float(line.split(":")[1].strip())*molar
            elif line.startswith("cation"):
                cation = line.split(":")[1].strip()
            elif line.startswith("anion"):
                anion = line.split(":")[1].strip()
            elif line.startswith("hydrogenMass"):
                hydrogenMass = float(line.split(":")[1].strip())*amu
            elif line.startswith("waterModel"):
                waterModel = line.split(":")[1].strip()
            elif line.startswith("rigidWater"):
                rigidWater = bool(line.split(":")[1].strip())
            elif line.startswith("step_size"):
                step_size = float(line.split(":")[1].strip())*femtoseconds
            elif line.startswith("temperature"):
                temperature = (float(line.split(":")[1].strip())+273.15)*kelvin
            elif line.startswith("pressure"):
                pressure = (float(line.split(":")[1].strip()))*bar
            elif line.startswith("eq_time"):
                eq_time = float(line.split(":")[1].strip())*picoseconds
            elif line.startswith("run_time"):
                run_time = float(line.split(":")[1].strip())*nanoseconds
            elif line.startswith("save_interval"):
                save_interval = float(line.split(":")[1].strip())*picoseconds
            elif line.startswith("backup_interval"):
                backup_interval = float(line.split(":")[1].strip())*60
            elif line.startswith("precision"):
                precision = line.split(":")[1].strip()

    settings = {'forcefield':forcefield, 'constraints':constraints, 'padding':padding,
                'ion_conc':ion_conc, 'cation':cation, 'anion':anion, 'hydrogenMass':hydrogenMass,
                'waterModel':waterModel, 'rigidWater':rigidWater, 'step_size':step_size,
                'temperature':temperature,'pressure':pressure, 'eq_time':eq_time,
                'run_time':run_time, 'save_interval':save_interval, 'backup_interval':backup_interval,
                'precision':precision}

    return settings


def prepare_simulation(save_at, status):

    """
    Prepares the system object. Adds solvent box if neccessary.
    Creates the simulation object and minimizes it.
    Returns the NGLViewer widget.
    """

    s = read_settings(save_at)

    if s['forcefield'] == "Amber14":
        if s['waterModel'] == "(explicit) TIP3P":
            ff = ForceField('amber14-all.xml', 'amber14/tip3p.xml')
            water = 'tip3p'
        elif s['waterModel'] == "(explicit) SPC/E":
            ff = ForceField('amber14-all.xml', 'amber14/spce.xml')
            water = 'spce'
        elif s['waterModel'] == "(explicit) TIP4P-Ew":
            ff = ForceField('amber14-all.xml', 'amber14/tip4pew.xml')
            water = 'tip4pew'
        elif s['waterModel'] == "(explicit) TIP5P":
            ff = ForceField('amber14-all.xml', 'tip5p.xml')
            water = 'tip5p'
        elif s['waterModel'] == "(explicit) OPC":
            ff = ForceField('amber14-all.xml', 'amber14/opc.xml')
            water = 'tip4pew'
        elif s['waterModel'] == "(explicit) OPC3":
            ff = ForceField('amber14-all.xml', 'amber14/opc3.xml')
            water = 'tip3p'
        elif s['waterModel'] == "(implicit) HCT (igb=1)":
            ff = ForceField('amber14-all.xml', 'implicit/hct.xml')
        elif s['waterModel'] == "(implicit) OBC1 (igb=2)":
            ff = ForceField('amber14-all.xml', 'implicit/obc1.xml')
        elif s['waterModel'] == "(implicit) OBC2 (igb=5)":
            ff = ForceField('amber14-all.xml', 'implicit/obc2.xml')
        elif s['waterModel'] == "(implicit) GBn (igb=7)":
            ff = ForceField('amber14-all.xml', 'implicit/gbn.xml')
        elif s['waterModel'] == "(implicit) GBn2 (igb=8)":
            ff = ForceField('amber14-all.xml', 'implicit/gbn2.xml')
        else:
            print("Error in reading the Amber14 forcefield parameters!")
            return None

    elif s['forcefield'] == "CHARMM36":
        if s['waterModel'] == "(explicit) TIP3P":
            ff = ForceField('charmm36.xml', 'charmm36/water.xml')
            water = 'tip3p'
        elif s['waterModel'] == "(explicit) SPC/E":
            ff = ForceField('charmm36.xml', 'charmm36/spce.xml')
            water = 'spce'
        elif s['waterModel'] == "(explicit) TIP4P-Ew":
            ff = ForceField('charmm36.xml', 'charmm36/tip4pew.xml')
            water = 'tip4pew'
        elif s['waterModel'] == "(explicit) TIP5P":
            ff = ForceField('charmm36.xml', 'charmm36/tip5p.xml')
            water = 'tip5p'
        elif s['waterModel'] == "(implicit) HCT (igb=1)":
            ff = ForceField('charmm36.xml', 'implicit/hct.xml')
        elif s['waterModel'] == "(implicit) OBC1 (igb=2)":
            ff = ForceField('charmm36.xml', 'implicit/obc1.xml')
        elif s['waterModel'] == "(implicit) OBC2 (igb=5)":
            ff = ForceField('charmm36.xml', 'implicit/obc2.xml')
        elif s['waterModel'] == "(implicit) GBn (igb=7)":
            ff = ForceField('charmm36.xml', 'implicit/gbn.xml')
        elif s['waterModel'] == "(implicit) GBn2 (igb=8)":
            ff = ForceField('charmm36.xml', 'implicit/gbn2.xml')
        else:
            print("Error in reading the CHARMM36 forcefield parameters!")
            return None

    elif s['forcefield'] == "AMOEBA 2018":
        if s['waterModel'].startswith("(explicit)"):
            ff = ForceField('amoeba2018.xml')
            water = 'tip3p'
        elif s['waterModel'].startswith("(implicit)"):
            ff = ForceField('amoeba2018.xml', 'amoeba2018_gk.xml')
        else:
            print("Error in reading the AMOEBA forcefield parameters!")
            return None

    else:
        print("Error in reading the forcefield parameters!")
        return None

    pdb = PDBFile(save_at+"protein_with_H.pdb")
    model = Modeller(pdb.topology, pdb.positions)

    if waterModel.startswith("(explicit)"):
        print("물 층을 더하는 중...", end='')

        if s['forcefield'] == "AMOEBA 2018":
            # AMOEBA forcefields somehow does not support NonbondedForce which is required to set the box dimensions from the padding distance.
            # As a detour, create the solvated system with Amber forcefield and then use that topology..
            ff2 = ForceField('amber14-all.xml', 'amber14/tip3p.xml')
            model2 = Modeller(pdb.topology, pdb.positions)
            model2.addExtraParticles(ff)
            model2.addSolvent(ff2, model='tip3p', padding=s['padding'], positiveIon=s['cation'],
                              negativeIon=s['anion'], ionicStrength=s['ion_conc'], neutralize=True)
            model = Modeller(model2.topology, model2.positions)
            model.addExtraParticles(ff)

        else:
            model.addExtraParticles(ff)
            model.addSolvent(ff, model=water, padding=s['padding'], positiveIon=s['cation'],
                             negativeIon=s['anion'], ionicStrength=s['ion_conc'], neutralize=True)
        print("완료.")

        print("계를 생성하는 중...", end='')

        if s['forcefield'] == "Amber14":
            system = ff.createSystem(model.topology, nonbondedMethod=PME,
                                 nonbondedCutoff=1.0*nanometer, constraints=s['constraints'],
                                 rigidWater=s['rigidWater'], removeCMMotion=True,
                                 hydrogenMass=s['hydrogenMass'])
        elif s['forcefield'] == "CHARMM36":
            # CHARMM forcefield recommends the use of switch distance at 1.0 nm and cutoff distance at 1.2 nm.
            system = ff.createSystem(model.topology, nonbondedMethod=PME,
                                     nonbondedCutoff=1.2*nanometer, constraints=s['constraints'],
                                     rigidWater=s['rigidWater'], removeCMMotion=True,
                                     switchDistance=1.0*nanometer,
                                     hydrogenMass=s['hydrogenMass'])
        else:
            # AMOEBA forcefields do not support constraints
            system = ff.createSystem(model.topology, nonbondedMethod=PME,
                                     nonbondedCutoff=1.0*nanometer, vdwCutoff=1.2*nanometer,
                                     constraints="None",
                                     rigidWater=False, removeCMMotion=True,
                                     polarization='extrapolated',
                                     hydrogenMass=s['hydrogenMass'])

    else:
        print("계를 생성하는 중...", end='')

        # Set solvent dielectric constant according to the empirical values
        """ Source : Hasted, J.B., Ritson, D.M., Collie, C.H.,
                    "Dielectric Properties of Aqueous Ionic Solutions. Parts I and II."
                    Journal of Chemical Physics 16, 1 (1948).
                    http://dx.doi.org/10.1063/1.1746645
        """

        if s['forcefield'] == "AMOEBA 2018":
            if s['cation'] == 'Li+':
                dcation = -11
            elif s['cation'] == 'Na+' or s['cation'] == 'K+':
                dcation = -8
            elif s['cation'] == 'Rb+' or s['cation'] == 'Cs+':
                dcation = -7

            if s['anion'] == 'F-':
                danion = -5
            elif s['anion'] == 'Cl-' or s['anion'] == 'Br-':
                danion = -3
            elif s['anion'] == 'I-':
                danion = -7

            dielectric = 80 + (dcation+danion)*s['ion_conc']/molar
            model.addExtraParticles(ff)
            system = ff.createSystem(model.topology, nonbondedMethod=NoCutoff,
                                     soluteDielectric=1.0, solventDielectric=dielectric,
                                     constraints="None", polarization="extrapolated",
                                     hydrogenMass=s['hydrogenMass'])
        else:
            # for other forcefields, setting the kappa value is possible
            # kappa is the inverse of Debye length.
            kappa = 367.434915*sqrt(s['ion_conc']/molar/78.5/(s['temperature']/kelvin))/nanometer
            model.addExtraParticles(ff)
            system = ff.createSystem(model.topology, nonbondedMethod=NoCutoff,implicitSolventKappa=kappa,
                                     constraints=s['constraints'], hydrogenMass=s['hydrogenMass'])

    # save the system as a serialized XML file.
    with open(save_at+'system.xml', 'w') as f:
        f.write(XmlSerializer.serialize(system))

    print("완료.")
    print("시뮬레이션을 생성하는 중...", end='')
    integrator = LangevinMiddleIntegrator(s['temperature'],1/picosecond, s['step_size'])

    platform = Platform.getPlatformByName('CUDA')
    properties = {'Precision': s['precision']}

    simulation = Simulation(model.topology, system, integrator, platform, properties)
    print("완료.")

    print("에너지 최적화 중...", end='')
    simulation.context.setPositions(model.positions)
    simulation.minimizeEnergy(tolerance=0.001*kilojoules/(nanometer*mole))
    positions = simulation.context.getState(getPositions=True).getPositions()
    with open(save_at+"minimized.pdb", 'w') as f:
        PDBFile.writeFile(simulation.topology, positions, f)
    print("완료.")

    w = nv.NGLWidget()
    w._set_size('750px','500px')
    w.add_component(nv.FileStructure(save_at+"minimized.pdb"))
    w.add_cartoon("protein or nucleic")
    if s['waterModel'].startswith("(explicit)"):
        w.add_point("water")
        w.add_spacefill("ion")
    w.center()

    # Initialize the simulation context
    simulation.context.setVelocitiesToTemperature(s['temperature'])
    simulation.context.setStepCount(0)
    simulation.context.setTime(0)
    simulation.saveCheckpoint(save_at+"checkpoint.chk")

    # Save the simulation context as a callable object in order to modify it on-the-fly
    status[4] = simulation

    if eq_time == 0:
        status[2] = "production"
        status[1] = "prepared"
        print("바로 7. Production Run 셀을 실행하세요.")
    else:
        status[2] = "NVT"
        status[1] = "prepared"
        print("5. NVT 평형 셀을 실행하세요.")

    return w


def update_status(save_at, status):
    """
    Updates the status variable, which contains the current status info of the simulation.
    Returns True for the started job
    """
    filelist = os.listdir(save_at[:-1])

    job_flag = [False, False, False]

    # Search the working directory for the trajectory files.
    for f in filelist:
        name = f.split('.')[0]
        ext = f.split('.')[-1]

        if ext == "xtc":
            if name.startswith("MD"):
                job_flag[2] = True
            elif name.startswith("NPT"):
                job_flag[1] = True
            elif name.startswith("NVT"):
                job_flag[0] = True

    if job_flag[2]:
        job = "production"
    elif job_flag[1]:
        job = "NPT"
    elif job_flag[0]:
        job = "NVT"
    else:
        job = None

    stride_flag = 0

    if job == "production":
        for f in filelist:
            name = f.split('.')[0]
            ext = f.split('.')[-1]
            if ext == "xtc" and name.startswith("MD"):
                stride = int(name.split("_")[-1])
                if stride > stride_flag:
                    stride_flag = stride

    status[2] = job
    status[3] = stride_flag

    if job is None:
        return False
    else:
        return True



def resume_simulation(save_at, status):
    """
    Resumes the simulation from the checkpoint.chk file.
    Returns True for the resumed job.
    """
    s = read_settings(save_at)

    status[0] = False

    if os.path.exists(save_at+"checkpoint.chk"):
        with open(save_at+'system.xml', 'r') as f:
            system = XmlSerializer.deserialize(f.read())

        # Somehow resuming from the state.xml does not work with MonteCarloBarostat.
        # Resumes from the checkpoint.chk and it is best to hope the device settings have not changed. :(
        integrator = LangevinMiddleIntegrator(s['temperature'],1/picosecond, s['step_size'])
        platform = Platform.getPlatformByName('CUDA')
        properties = {'Precision': s['precision']}
        pdb = PDBFile(save_at+"minimized.pdb")
        status[4] = Simulation(pdb.topology, system, integrator, platform, properties)

        print("checkpoint.chk로부터 시뮬레이션을 불러오는 중...", end='')
        status[4].loadCheckpoint(save_at+"checkpoint.chk")
        print("완료.")

        if status[2] == "NVT" or status[2] == "NPT":
            total_steps = int(s['eq_time']/s['step_size'])
        else:
            total_steps = int(s['run_time']/s['step_size'])

        if status[4].context.getStepCount() < total_steps:
            status[1] = "running"
            return True

        else:
            status[1] = "finished"
            return False

    else:
        print("checkpoint.chk 파일이 없습니다!")
        print("불러오기에 실패하였습니다. 새폴더를 생성해서 다시 처음부터 진행하세요.")
        return False


# When returning from the connection losses, check whether variables are alive.
if 'save_at' not in vars():
    print("1. 작업 폴더 지정 셀을 다시 실행하고 실행 결과를 따라가세요.")

else:
    s =  read_settings(save_at)

    if s is None:
        print("MD 설정값이 없습니다.")
        print("3. MD 조건 설정 셀을 다시 실행해주세요.")

    else:
        # status variable
        # status[0] : checks for the halt
        # status[1] : shows the current state of simultion (prepared, started, running, or finished)
        # status[2] : shows the current stage of simulation (NVT, NPT, or production)
        # status[3] : shows the current stride of the production run (MD production trajectory files are splitted into strides in case of disconnections)
        # status[4] : simulation object

        status = [False, "prepared", None, 0, None]

        if not update_status(save_at, status):
            print("기존 trajectory 파일이 없습니다. 새로 시뮬레이션을 시작합니다.")
            view3 = prepare_simulation(save_at, status)
            if view3 is None:
                print("MD 조건 설정을 다시해주세요.")
            else:
                display(view3)

        else:
            if resume_simulation(save_at, status):
                if status[2] == "NVT":
                    print("5. NVT 평형으로 가세요.")
                elif status[2] == "NPT":
                    print("6. NPT 평형으로 가세요.")
                else:
                    print("7. Production Run으로 가세요.")
            else:
                if status[2] == "NVT" and s['waterModel'].startswith("(explicit)"):
                    print("6. NPT 평형으로 가세요.")
                elif status[2] == "NPT" or (status[2] == "NVT" and s['waterModel'].startswith("(implicit)")):
                    print("7. Production Run으로 가세요.")
                else:
                    print("모든 MD 계산이 끝났습니다.")
                    print("8. 결과 분석으로 가세요.")

기존 trajectory 파일이 없습니다. 새로 시뮬레이션을 시작합니다.
물 층을 더하는 중...완료.
계를 생성하는 중...완료.
시뮬레이션을 생성하는 중...완료.
에너지 최적화 중...완료.
5. NVT 평형 셀을 실행하세요.


NGLWidget()

In [ ]:
#@title #5. NVT 평형

def NVT_equilibrate(save_at, status):
    """
    Runs NVT equilibration.
    Returns True if the equilibration has been performed.
    """

    if status[2] == "NVT" and status[1] == "finished":
        print("NVT 평형이 이미 끝났습니다.")
        return False

    elif status[2] == "NPT" or status[2] == "production":
        print("NVT 평형 이후 단계가 이미 진행중입니다.")
        return False

    s = read_settings(save_at)

    total_steps = int(s['eq_time']/s['step_size'])

    if total_steps == 0:
        print("eq_time이 0 ps로 지정되어서 평형 단계가 생략됩니다.")
        return False

    step = status[4].context.getStepCount()

    if step >= total_steps:
        print(f'NVT 평형이 이미 {s["eq_time"]}만큼 진행되었습니다.')
        print("eq_time을 3. MD 조건 설정에서 늘리고 4. 시뮬레이션 준비를 실행 후 이 셀을 실행해주세요.")
        return False

    status[4].reporters.clear()

    logger = StateDataReporter(status[2]+"_log.txt", 10, step=True,
                               potentialEnergy=True, kineticEnergy=True,
                               temperature=True, separator=',')

    save = int(s['save_interval']/s['step_size'])

    if s['waterModel'].startswith("(explicit)"):
        box = True
    else:
        box = False

    if os.path.exists(save_at+status[2]+".xtc"):
        append = True
    else:
        append = False

    xtc = XTCReporter(save_at+status[2]+".xtc", save, append=append,
                      enforcePeriodicBox=box)

    status[4].reporters.append(logger)
    status[4].reporters.append(xtc)

    if step == 0:
        print("NVT 평형을 시작합니다.")
    else:
        print("NVT 평형을 이어갑니다.")

    status[1] = "running"
    for i in tqdm_notebook(range(total_steps-step)):
        status[4].step(1)

    status[4].saveCheckpoint(save_at+"checkpoint.chk")

    print("NVT 평형이 끝났습니다.")
    status[1] = "finished"

    return True

if NVT_equilibrate(save_at, status):
    time = []
    temp = []
    s = read_settings(save_at)

    with open("NVT_log.txt", 'r') as f:
        for line in f.readlines():
            if line.startswith("#"):
                continue
            line = line.strip().split(',')
            step = float(line[0])
            time.append(step*s['step_size']/picoseconds)
            temp.append(round(float(line[3]),2))

    target_temp = round(s['temperature']/kelvin,2)

    fig1 = go.Figure()
    fig1.add_trace(go.Scatter(x=time, y=temp, mode='lines', name='Temperature'))
    fig1.add_hline(y=target_temp, annotation_text="target T : "+str(target_temp)+" K")
    fig1.update_layout(title='NVT equilibration', xaxis_title='Time (ps)', yaxis_title='Temperature (K)', width=750, height=500)
    fig1.show()

    print("계의 온도가 일정한 값에 수렴하는지 확인해주세요.")
    print("아니라면 3. MD 조건 설정에서 eq_time 변수를 키운 뒤 해당 셀부터 다시 진행해주세요.")
else:
    print("다음 셀로 진행하세요.")

NVT 평형을 시작합니다.


  0%|          | 0/40000 [00:00<?, ?it/s]

NVT 평형이 끝났습니다.


계의 온도가 일정한 값에 수렴하는지 확인해주세요.
아니라면 3. MD 조건 설정에서 eq_time 변수를 키운 뒤 해당 셀부터 다시 진행해주세요.


In [ ]:
#@title #6. NPT 평형

def NPT_equilibrate(save_at, status):
    """
    Runs NPT equilibration.
    Returns True if the equilibration has been performed.
    """

    if status[2] == "NVT" and status[1] != "finished":
        print("NVT 평형부터 마저 마치고 오세요.")
        return False

    elif status[2] == "NPT" and status[1] == "finished":
        print("NPT 평형이 이미 끝났습니다.")
        print("7. Production Run으로 가세요.")
        return False

    elif status[2] == "production":
        print("다음 단계인 Production Run이 이미 진행중입니다.")
        return False

    s = read_settings(save_at)

    if s['waterModel'].startswith("(implicit)"):
        print("implicit 용매 모델에서는 부피가 정의되지 않아 NPT 평형이 불가합니다.")
        print("7. Production Run으로 가세요.")
        return False

    total_steps = int(s['eq_time']/s['step_size'])

    if total_steps == 0:
        print("eq_time이 0 ps라 평형 단계가 생략됩니다.")
        print("7. Production Run으로 가세요.")
        return False

    if status[2] == "NVT" and status[1] == "finished":
        print("NPT 평형을 시작합니다.")
        status[2] = "NPT"
        status[4].context.setStepCount(0)
        status[4].context.setTime(0)
        force = MonteCarloBarostat(s['pressure'], s['temperature'])
        status[4].system.addForce(force)
        # The context should be reinitialized after adding a force.
        status[4].context.reinitialize(preserveState=True)
        # Update the system.xml file.
        with open(save_at+'system.xml', 'w') as f:
            f.write(XmlSerializer.serialize(status[4].system))
        append = False
    else:
        print("NPT 평형을 이어갑니다.")
        append = True

    status[4].reporters.clear()
    step = status[4].context.getStepCount()

    if step >= total_steps:
        print(f'이미 NPT 평형이 {s["eq_time"]}만큼 진행되었습니다.')
        print("eq_time을 늘리고 3. MD 조건 설정 -> 4. 시뮬레이션 준비를 실행 후 이 셀을 실행하세요.")
        return False

    save = int(s['save_interval']/s['step_size'])

    logger = StateDataReporter(status[2]+"_log.txt", 10, potentialEnergy=True,
                               kineticEnergy=True, temperature=True,
                               volume=True, density=True, step=True)

    xtc = XTCReporter(save_at+status[2]+".xtc", save, append=append,
                      enforcePeriodicBox=True)

    status[4].reporters.append(logger)
    status[4].reporters.append(xtc)

    status[1] = "started"
    for i in tqdm_notebook(range(total_steps-step)):
        status[4].step(1)

    status[4].saveCheckpoint(save_at+"checkpoint.chk")
    print("NPT 평형이 완료되었습니다.")
    status[1] = "finished"

    return True

if NPT_equilibrate(save_at, status):
    time = []
    temp = []
    dens = []

    with open("NPT_log.txt", 'r') as f:
        for line in f.readlines():
            if line.startswith("#"):
                continue
            line = line.strip().split(',')
            step = float(line[0])
            time.append(step*s['step_size']/picoseconds)
            temp.append(round(float(line[3]),2))
            dens.append(round(float(line[5]),5))

    target_temp = round(s['temperature']/kelvin,2)

    fig2 = make_subplots(specs=[[{"secondary_y":True}]])
    fig2.add_trace(go.Scatter(x=time, y=temp, mode='lines', name='Temperature'), secondary_y=False)
    fig2.add_hline(y=target_temp, annotation_text="target T : "+str(target_temp)+" K")
    fig2.add_trace(go.Scatter(x=time, y=dens, mode='lines', name='Density'), secondary_y=True)
    fig2.update_layout(title='NPT equilibration', width=750, height=500)
    fig2.update_xaxes(title_text="Time (ps)")
    fig2.update_yaxes(title_text="Temperature (K)", secondary_y=False)
    fig2.update_yaxes(title_text="Density (g/mL)", secondary_y=True)
    fig2.show()

    print("계의 온도와 밀도가 일정한 값으로 수렴하는지 확인해주세요.")
    print("아니라면, eq_time을 늘린 뒤 3. MD 조건 설정 -> 4. 시뮬레이션 준비 -> 6. NPT 평형 순으로 실행해주세요.")

NPT 평형을 시작합니다.


  0%|          | 0/40000 [00:00<?, ?it/s]

NPT 평형이 완료되었습니다.


계의 온도와 밀도가 일정한 값으로 수렴하는지 확인해주세요.
아니라면, eq_time을 늘린 뒤 3. MD 조건 설정 -> 4. 시뮬레이션 준비 -> 6. NPT 평형 순으로 실행해주세요.


In [ ]:
#@title #7. Production Run
#@markdown 데이터를 얻기 위한 MD production run을 시작합니다.

#@markdown 이 셀을 실행하면 밑에 빈 위젯이 뜹니다. 그 다음 셀을 실행해서 실시간 진행 상황을 확인할 수 있습니다.

#@markdown 실시간 구조 스냅샷은 메모리가 많이 요구되니, update_period 값을 일단 60초로 맞췄다가 천천히 줄여보세요.

#@markdown update_period를 0초로 설정하면 위젯에 스냅샷이 더이상 표시되지 않습니다.

#@markdown 스냅샷 상으로 구조가 가끔 이상하게 뜰 수 있습니다. 나중에 trajectory는 멀쩡할겁니다.

#@markdown 텍스트로 표시되는 실시간 진행 상황은 1초마다 계속 표시됩니다.

def check_thread():
    """
    Checks whether the simulation is running in the background.
    Returns True if the simulation is running.
    """
    warnings.filterwarnings("ignore")
    simulationIsRunning = False
    for t in threading.enumerate():
        if t.name == "MD":
            simulationIsRunning = True
            break
    return simulationIsRunning


def run_simulation(save_at, total_steps, box, save_period, backup_interval, status):
    """
    Runs the MD simulation.
    Generates a stride of trajectory.xtc file for each backup_intervals.
    """
    while not status[0]:
        current_step = status[4].context.getStepCount()

        if current_step == 0 or not os.path.exists("MD_log.txt"):
            if current_step == 0:
                status[1] = "started"
            elif current_step < total_steps:
                status[1] = "running"
            else:
                status[1] = "finished"
                print("시뮬레이션의 길이가 지정된 시간에 도달했습니다.")
                break

            logger = StateDataReporter("MD_log.txt", 50, append=False, step=True,
                                       potentialEnergy=True, temperature=True,
                                       progress=True, remainingTime=True,
                                       speed=True, elapsedTime=True,
                                       totalSteps=total_steps)

        elif current_step < total_steps:
            status[1] = "running"
            logger = StateDataReporter("MD_log.txt", 50, append=True, step=True,
                                       potentialEnergy=True, temperature=True,
                                       progress=True, remainingTime=True,
                                       speed=True, elapsedTime=True,
                                       totalSteps=total_steps)

        else:
            status[1] = "finished"
            print("시뮬레이션이 끝났습니다.")
            break


        xtc = XTCReporter(save_at+"MD_"+str(status[3])+".xtc", save_period, append=False,
                          enforcePeriodicBox=box)

        status[4].reporters.clear()
        status[4].reporters.append(logger)
        status[4].reporters.append(xtc)

        # Run for backup_interval minutes and then save the progress
        for i in range(int(backup_interval)):
            status[4].runForClockTime(1*second)
            if status[0]:
                break
            elif status[4].context.getStepCount() >= total_steps:
                break

        status[4].saveCheckpoint(save_at+"checkpoint.chk")
        status[3] += 1

    return


def production_run(save_at, status):
    """
    Performs the production run.
    Returns True if the run has been performed.
    """
    if status[1] != "finished" and status[2] != "production":
        print("평형 단계부터 먼저 마쳐주세요.")
        return False

    elif status[1] == "finished" and status[2] == "production":
        print("Production Run이 이미 끝났습니다.")
        print("8. 결과 분석으로 가세요.")
        return False

    elif check_thread():
        print("시뮬레이션이 백그라운드에서 실행중입니다.")
        return True

    elif status[0]:
        print("일시중지된 시뮬레이션을 다시 시작합니다.")
        resume_simulation(save_at, status)
        s = read_settings(save_at)

        total_steps = int(s['run_time']/s['step_size'])
        save_period = int(s['save_interval']/s['step_size'])

        if s['waterModel'].startswith("(explicit)"):
            box = True
        else:
            box = False

        status[2] = "production"
        status[1] = "running"

        # Enables the background calculation process
        # It is impossible to run two or more cells simultaneously in Colab, so this was the solution I came up with..
        t = threading.Thread(name="MD", target=run_simulation,
                             args=(save_at, total_steps, box,
                                   save_period, s['backup_interval'], status,))
        t.setDaemon(False)
        t.start()
        return True

    else:
        if status[1] == "finished" and status[2] != "production":
            status[4].context.setStepCount(0)
            status[4].context.setTime(0)

        s = read_settings(save_at)

        total_steps = int(s['run_time']/s['step_size'])
        save_period = int(s['save_interval']/s['step_size'])

        if s['waterModel'].startswith("(explicit)"):
            box = True
        else:
            box = False

        status[2] = "production"
        status[1] = "running"

        t = threading.Thread(name="MD", target=run_simulation,
                             args=(save_at, total_steps, box,
                                   save_period, s['backup_interval'], status,))
        t.setDaemon(False)
        t.start()
        print("시뮬레이션이 백그라운드에서 실행됩니다.")
        return True

if production_run(save_at, status):
    view4 = nv.NGLWidget()
    view4._set_size('750px','500px')
    view4.add_structure(nv.FileStructure(save_at+"minimized.pdb"), defaultRepresentation=False)
    display(view4)

시뮬레이션이 백그라운드에서 실행됩니다.


NGLWidget()

In [ ]:
update_period = 60 #@param {type:"slider", min:0, max:60, step:5}
#@markdown 백그라운드에서 진행 중인 시뮬레이션을 중단하고 싶으면 아래 박스를 체크하세요.
halt_simulation = False #@param {type:"boolean"}

def display_simulation(save_at, status, w, t, halt):
    """
    Displays the current state/snapshot of the simulation.
    """
    status[0] = halt

    if halt:
        print("시뮬레이션이 사용자에 의해 중단되었습니다.")
        print("다시 이어가려면 위 셀을 다시 실행하세요.")
        return

    if not check_thread():
        print("진행 중인 계산이 없습니다.")
        return

    s = read_settings(save_at)

    if s['waterModel'].startswith("(explicit)"):
        box = True
    else:
        box = False

    # Reads the MD_log.txt file and reports the tail
    log = open("MD_log.txt", 'r')
    log.seek(0,2)
    wait = 0
    counter = 0

    w.clear_representations()
    w.add_cartoon("protein or nucleic", lowResolution=True, antialias=False)
    if box:
        w.add_spacefill("ion", lowResolution=True, antialias=False)
        w.add_point("water", lowResolution=True, antialias=False)

    try:
        while True:
            if status[1] == "finished":
                print("\t시뮬레이션이 끝났습니다..")
                print("8. 결과 분석으로 가세요.")
                break

            where = log.tell()
            line = log.readline()

            if not line:
                sleep(0.1)
                wait += 1
                log.seek(where)
                if wait > 50:
                    print("시뮬레이션이 응답하지 않습니다.")
                    break

            elif line.startswith("#"):
                continue

            elif not line.endswith("\n"):
                continue

            else:
                data = line.strip().split(',')
                if len(data) < 7:
                    continue
                print(f'{data[0]:>6s} done, {data[6]} left. Step : {data[1]}, Potential Energy : {float(data[2]):.2f} kJ/mol, Temperature : {(float(data[3])-273.15):.2f} C, Speed : {data[4]} ns/day', end='')
                wait = 0
                counter += 1

                if t != 0:
                    # Update the snapshot every t seconds.
                    if counter % t == 0:
                        state = status[4].context.getState(getPositions=True, enforcePeriodicBox=box)
                        position = state.getPositions(asNumpy=True)
                        w.set_coordinates({0:position*10})
                        w.update_representation(component=0)
                        w.center()

                log.seek(0,2)
                sleep(1)
                # Renew the output
                print(" ", end='\r')

    except KeyboardInterrupt:
        print("\t현황 업데이트가 중단되었습니다..")
        log.close()
        return

    log.close()
    return


if 'save_at' in vars():
    display_simulation(save_at, status, view4, update_period, halt_simulation)
else:
    print("1. 작업 폴더 지정부터 다시 실행해주세요.")

 99.3% done, 0:01 left. Step : 397150, Potential Energy : -137534.40 kJ/mol, Temperature : 24.39 C, Speed : 413 ns/day시뮬레이션이 끝났습니다.
	시뮬레이션이 끝났습니다..
8. 결과 분석으로 가세요.


In [ ]:
#@title #8. 결과 분석
#@markdown 아래의 다른 분석들을 실행하기 전에 이 셀을 실행해주세요.

#@markdown 아래 위젯의 재생버튼을 눌러 trajectory를 애니메이션으로 확인할 수 있습니다.

def wrap_trajectory(save_at, status):
    """
    Wraps the trajectory and concatenates the trajectory files.
    """
    print("trajectory 파일들을 읽어들이는 중...", end='')
    trajs = []
    for i in range(status[3]):
        trajs.append(save_at+'MD_'+str(i)+'.xtc')

    traj = md.load(trajs, top=save_at+'minimized.pdb')
    print("완료.")

    s = read_settings(save_at)
    prot_indices = traj.topology.select("protein")

    if s['waterModel'].startswith("(explicit)"):
        print("PBC 박스 내로 분자들을 재배치 중...", end='')
        if len(prot_indices) > 0:
            prot = traj.topology.subset(prot_indices)
            traj.image_molecules(inplace=True, anchor_molecules=prot.find_molecules())
        else:
            traj.image_molecules(inplace=True, anchor_molecules=traj.topology.guess_anchor_molecules())
        print("완료.")

    print("위치 보정 중...", end='')
    if len(prot_indices) > 0:
        traj2 = traj.superpose(traj, 0, atom_indices=traj.topology.select_atom_indices('alpha'))
    else:
        traj2 = traj.superpose(traj, 0, atom_indices=traj.topology.select_atom_indices('heavy'))

    print("완료.")
    print("보정된 trajectory를 'MD_processed.xtc'에 저장합니다...", end='')
    traj2.save_xtc(save_at+'MD_processed.xtc')
    traj2[0].save_pdb(save_at+'MD_processed_0.pdb')
    print("완료.")

    return

if 'save_at' not in vars():
    print("1. 작업 폴더 지정부터 다시 실행하세요.")

elif os.path.exists(save_at+'MD_processed.xtc'):
    traj = md.load(save_at+'MD_processed.xtc', top=save_at+'MD_processed_0.pdb')
    prot_traj = traj.atom_slice(traj.topology.select("not water"))
    view5 = nv.show_mdtraj(prot_traj, defaultRepresentation=False)
    view5._set_size('750px','500px')
    view5.add_cartoon("protein or nucleic", lowResolution=True)
    view5.add_simplified_base("nucleic", lowResolution=True, color_scheme='chainindex')
    view5.center()
    display(view5)

else:
    wrap_trajectory(save_at, status)
    traj = md.load(save_at+'MD_processed.xtc', top=save_at+'MD_processed_0.pdb')
    prot_traj = traj.atom_slice(traj.topology.select("not water"))
    view5 = nv.show_mdtraj(prot_traj, defaultRepresentation=False)
    view5._set_size('750px','500px')
    view5.add_cartoon("protein or nucleic", lowResolution=True)
    view5.add_simplified_base("nucleic", lowResolution=True, color_scheme='chainindex')
    view5.center()
    display(view5)

NGLWidget(max_frame=99)

In [ ]:
#@title Clustering
#@markdown RMSD 기준 값 (nm)을 정하면 이보다 작은 RMSD를 갖는 구조들이 한 덩어리로 묶입니다.
rmsd_threshold = 0.1 #@param {type:"slider", min:0.1, max:1.0, step:0.05}

#@markdown 각 뭉치들의 대표 구조 (중심 구조)들이 "clustered.pdb"의 다른 프레임에 저장됩니다.

rmsd_matrix = np.zeros((traj.n_frames, traj.n_frames))

for i in tqdm_notebook(range(traj.n_frames)):
    rmsd_matrix[i] = md.rmsd(traj, traj, frame=i, atom_indices=traj.topology.select_atom_indices('heavy'))

clustering = AgglomerativeClustering(n_clusters=None, distance_threshold=rmsd_threshold, metric='precomputed', linkage='average')
cluster_labels = clustering.fit_predict(rmsd_matrix)

n_clusters = len(set(cluster_labels))
cluster_sizes = Counter(cluster_labels)
sorted_clusters = sorted(cluster_sizes.items(), key=lambda x:x[1], reverse=True)

print(f"Total {n_clusters} clusters found!")

centroids = []
for cluster, size in sorted_clusters:
    cluster_frames = np.where(cluster_labels == cluster)[0]
    centroid_idx = cluster_frames[np.argmin([np.sum(rmsd_matrix[frame, cluster_frames]) for frame in cluster_frames])]
    print(f"Cluser {cluster} (size = {size})'s centroid structure : frame {centroid_idx}")
    centroids.append((cluster, size, centroid_idx))

cent_traj = md.join([traj[idx] for _, _, idx in centroids])
cent_traj.save_pdb(save_at+"clustered.pdb")

view6 = nv.show_mdtraj(cent_traj, defaultRepresentation=False)
view6._set_size('750px','500px')
view6.add_cartoon("protein or nucleic")
view6.add_licorice("protein or nucleic")
view6.center()
view6.player.delay = 3000
display(view6)

  0%|          | 0/100 [00:00<?, ?it/s]

Total 2 clusters found!
Cluser 0 (size = 97)'s centroid structure : frame 84
Cluser 1 (size = 3)'s centroid structure : frame 20


NGLWidget(max_frame=1)

In [ ]:
#@title Backbone Root-Mean-Square Deviation
#@markdown Trajectory의 첫 프레임과 비교했을 때 backbone 원자들의 좌표로 계산한 RMSD값 변화를 나타낸 그래프입니다.

rmsd = md.rmsd(traj, traj, 0, atom_indices=traj.topology.select_atom_indices('minimal'))

fig3 = go.Figure()
fig3.add_trace(go.Scatter(x=traj.time/1000, y=rmsd, mode='lines', name='RMSD'))
fig3.update_layout(title='Backbone RMSD', xaxis_title='Time (ns)', yaxis_title='RMSD (nm)', width=750, height=500)
fig3.show()

In [ ]:
#@title Radius of Gyration
#@markdown 단백질/핵산 분자의 회전 반경 변화를 나타냅니다.

rg = md.compute_rg(traj)

fig4 = go.Figure()
fig4.add_trace(go.Scatter(x=traj.time/1000, y=rg, mode='lines', name='RoG'))
fig4.update_layout(title='Radius of Gyration', xaxis_title='Time (ns)', yaxis_title='Radius of Gyration (nm)', width=750, height=500)
fig4.show()

In [ ]:
#@title Residue-wise Root-Mean-Square Fluctuation
#@markdown Residue별 모든 원자들의 좌표로부터 계산한 RMSF 값을 보여줍니다.

#@markdown RMSF가 큰 residue는 더 이리저리 많이 움직인다는 것을 뜻합니다.

prot_indices = traj.topology.select("not water and (mass 11 to 33) and (symbol != 'Na')")
traj2 = traj.superpose(traj, 0, atom_indices=prot_indices)
traj2.atom_slice(atom_indices=prot_indices, inplace=True)

atom_rmsf = np.sqrt(3*np.mean(np.square(traj2.xyz - np.mean(traj2.xyz, axis=0)), axis=0))

res_rmsf = []
for residue in traj2.topology.residues:
    atom_idx = [atom.index for atom in residue.atoms]
    res_rmsf.append(np.mean(atom_rmsf[atom_idx]))

fig5 = go.Figure()
fig5.add_trace(go.Scatter(x=np.arange(traj2.topology.n_residues), y=res_rmsf, mode='lines', name='RMSF',
                          hovertemplate='Residue: %{x}<br>RMSF: %{y:.3f} nm<extra></extra>'))
fig5.update_layout(title='Residue-wise Root-Mean-Square Fluctuation', xaxis_title='Residue index', yaxis_title='RMSF (nm)',
                   hovermode='closest', width=750, height=500)
fig5.show()

In [ ]:
#@title 2차원 주성분 분석
#@markdown 원자들의 집합적인 운동을 직교벡터 성분들로 추출해서 가장 고윳값이 큰 벡터들을 주성분이라고 부릅니다. 고윳값은 그 주성분이 갖는 설명력이라고 할 수 있습니다.

prot_indices = traj.topology.select("not water and (mass 11 to 33) and (symbol != 'Na')")
traj2 = traj.superpose(traj, 0, atom_indices=prot_indices)
pca = PCA(n_components=2)
reduced_cart = pca.fit_transform(traj2.xyz.reshape(traj2.n_frames, traj2.topology.subset(prot_indices).n_atoms*3))
var_explained = pca.explained_variance_ratio_*100

s = read_settings(save_at)

fig6 = go.Figure()
fig6.add_trace(go.Scatter(x=reduced_cart[:,0], y=reduced_cart[:,1], mode='markers',
                          marker=dict(size=5, color=np.arange(len(reduced_cart))*s["save_interval"]/1000, colorscale='Viridis', colorbar=dict(title='Time (ns)'), showscale=True),
                          text=[f'Time: {i*s["save_interval"]}' for i in range(len(reduced_cart))], hoverinfo='text', name='PCA'))
fig6.update_layout(title='Two Dimensional Principal Component Analysis', xaxis_title=f'PC1 ({var_explained[0]:.2f}%)', yaxis_title=f'PC2 ({var_explained[1]:.2f}%)', width=750, height=500)
fig6.show()

In [ ]:
#@title 3차원 주성분 분석

prot_indices = traj.topology.select("not water and (mass 11 to 33) and (symbol != 'Na')")
traj2 = traj.superpose(traj, 0, atom_indices=prot_indices)
pca = PCA(n_components=3)
reduced_cart = pca.fit_transform(traj2.xyz.reshape(traj2.n_frames, traj2.topology.subset(prot_indices).n_atoms*3))
var_explained = pca.explained_variance_ratio_*100

s = read_settings(save_at)

fig7 = go.Figure()
fig7.add_trace(go.Scatter3d(x=reduced_cart[:,0], y=reduced_cart[:,1], z=reduced_cart[:,2], mode='markers',
                          marker=dict(size=5, color=s["save_interval"]/1000*np.arange(len(reduced_cart)), colorscale='Viridis', opacity=0.8, colorbar=dict(title='Time (ns)'), showscale=True),
                          text=[f'Time: {i*s["save_interval"]}' for i in range(len(reduced_cart))], hoverinfo='text', name='PCA'))
fig7.update_layout(title='Three Dimensional Principal Component Analysis', scene=dict(xaxis_title=f'PC1 ({var_explained[0]:.2f}%)', yaxis_title=f'PC2 ({var_explained[1]:.2f}%)', zaxis_title=f'PC3 ({var_explained[2]:.2f}%)'), width=750, height=750)
fig7.show()

In [ ]:
#@title 주성분 시각화
#@markdown 각 주성분이 어떤 운동을 나타내는지 시각화해줍니다.

#@markdown 보고 싶은 주성분의 번호를 골라보세요.
component_to_view = "1" #@param [1, 2, 3, 4, 5, 6, 7, 8, 9, 10]
#@markdown 운동의 크기를 지정해주세요. 클 수록 눈에 잘 띄지만 너무 커지면 구조가 안뜰 수 있습니다.
scale = 3 #@param {type:"slider", min:1, max:10, step:1}

prot_indices = traj.topology.select("not water and (mass 11 to 33) and (symbol != 'Na')")
traj2 = traj.superpose(traj, 0, atom_indices=prot_indices)
traj2.atom_slice(atom_indices=prot_indices, inplace=True)
coords = traj2.xyz.reshape(traj2.n_frames, -1)

pca = PCA()
pca_results = pca.fit_transform(coords)
top_pcs = pca.components_[:10]

pc_trajs = top_pcs.reshape(10, traj2.n_atoms, 3)
sine_wave = np.sin(np.linspace(0, 2*np.pi, num=50))

pc_traj = md.Trajectory(np.zeros((50, traj2.n_atoms, 3)), traj2.topology)

for i in range(50):
    pc_traj.xyz[i] = traj2.xyz[0] + scale*sine_wave[i]*pc_trajs[int(component_to_view)-1]

view7 = nv.show_mdtraj(pc_traj, defaultRepresentation=False)
view7._set_size('750px','500px')
view7.add_cartoon("protein or nucleic", lowResolution=True, color_scheme='residueindex')
view7.add_simplified_base("nucleic", lowResolution=True, color_scheme='residueindex')
view7.center()
view7.player.delay = 500
display(view7)

NGLWidget(max_frame=49)

In [ ]:
#@title Ramachandran Map
#@markdown 단백질의 backbone 원자들이 이루는 이면각들인 phi와 psi 값을 보여주는 Ramachandran diagram을 그려줍니다.

#@markdown 큰 단백질의 경우 로딩이 오래 걸릴 수 있습니다.

stride = int(traj.n_frames/50)

if stride < 2:
    traj2 = traj
    stride = 1
else:
    traj2 = traj[::stride]

phi = md.compute_phi(traj2, periodic=False)[1]
psi = md.compute_psi(traj2, periodic=False)[1]

s = read_settings(save_at)

fig8 = go.Figure()
colors = np.linspace(0, traj.n_frames*s['save_interval'].value_in_unit(nanosecond), traj2.n_frames)

fig8.add_trace(go.Scatter(x=phi.flatten(), y=psi.flatten(), mode='markers', marker=dict(color=np.repeat(colors, phi.shape[1]), colorscale='Viridis', colorbar=dict(title='Time (ns)'), showscale=True),
                          text=[f'Time: {(i//phi.shape[1])*stride*s["save_interval"]}<br>Residue: {i%phi.shape[1]}<br>Phi: {phi[i//phi.shape[1], i%phi.shape[1]]:.2f}<br>Psi: {psi[i//phi.shape[1], i%phi.shape[1]]:.2f}'
                                for i in range(phi.size)], hoverinfo='text'))

fig8.update_layout(title='Time-dependent Ramachandran Map', xaxis_title='Phi (radians)', yaxis_title='Psi (radians)', xaxis_range=[-np.pi, np.pi], yaxis_range=[-np.pi, np.pi], width=750, height=500)
fig8.show()

In [ ]:
#@title Solvent Accessible Surface Area
#@markdown 주어진 residue가 용매와 접촉하는 면적을 보여줍니다.

#@markdown 보고 싶은 residue의 번호를 입력하세요.

residue_index = "6" #@param {type:"string"}

res_idx = int(residue_index)-1

if res_idx < 0 or res_idx >= traj.topology.n_residues:
    print("Invalid residue index!")

else:
    sasa = md.shrake_rupley(traj, mode='residue')

    fig9 = go.Figure()
    fig9.add_trace(go.Scatter(x=traj.time/1000, y=sasa[:,res_idx], mode='lines', name='SASA'))
    fig9.update_layout(title=f'Solvent Accessible Surface Area of the residue {traj.topology.residue(res_idx)}', xaxis_title='Time (ns)', yaxis_title='SASA (nm^2)', width=750, height=500)
    fig9.show()

In [ ]:
#@title DSSP를 통한 2차구조 분석
#@markdown Define Secondary Structure of Proteins 알고리즘을 이용해 각 residue가 갖는 2차구조를 보여줍니다.

dssp = md.compute_dssp(traj)
dssp_map = {'H':0, 'E':1, 'C':2}
dssp_num = np.array([[dssp_map.get(ss,2) for ss in frame] for frame in dssp])

s = read_settings(save_at)

fig10 = go.Figure(data=go.Heatmap(z=dssp_num.T, x=traj.time/1000, y=np.arange(traj.n_residues),
                                 colorscale=[[0,'red'],[0.33, 'red'], [0.33, 'yellow'], [0.66, 'yellow'], [0.66, 'blue'], [1, 'blue']],
                                 colorbar=dict(tickvals=[0,1,2],ticktext=['Helix', 'Sheet', 'Coil'])))
fig10.update_layout(title='Time-dependent Secondary Structure (DSSP)', xaxis_title='Time (ns)', yaxis_title='Residue index', width=750, height=1000)
fig10.data[0].hovertext = [[f'Time : {i*s["save_interval"]}<br>Residue: {j}<br>SS: {dssp[i][j]}' for i in range(traj.n_frames)] for j in range(traj.n_residues)]
fig10.data[0].hoverinfo = 'text'
fig10.show()

In [ ]:
#@title Dynamic Cross-Correlation Matrix
#@markdown 각 residue쌍의 알파탄소의 운동의 상관관계를 그린 표입니다.

#@markdown 파랑색 (+1)에 가까울 수록 양의 상관관계가 큰 것이고, 두 residue가 같은 방향으로 움직이는 경향이 있다는 뜻입니다.

#@markdown 빨강색 (-1)에 가까울 수록 음의 상관관계가 큰 것이고, 두 residue가 반대 방향으로 움직이는 경향이 있다는 뜻입니다.

#@markdown 흰색 (0)에 가까울 수록 상관관계가 없는 것이고, 두 residue가 독립적으로 움직인다는 뜻입니다.

ca_idx = traj.topology.select_atom_indices('alpha')
mean_pos = np.mean(traj.xyz[:, ca_idx, :], axis=0)
fluct = traj.xyz[:, ca_idx, :] - mean_pos

dccm = np.zeros((traj.n_residues, traj.n_residues))

for i in range(traj.n_residues):
    for j in range(traj.n_residues):
        numerator = np.mean(np.sum(fluct[:,i,:]*fluct[:,j,:], axis=1))
        denominator = np.sqrt(np.mean(np.sum(fluct[:,i,:]**2, axis=1))*np.mean(np.sum(fluct[:,j,:]**2, axis=1)))
        dccm[i,j] = numerator/denominator

fig11 = go.Figure(data=go.Heatmap(z=dccm, colorscale='RdBu', zmid=0, colorbar=dict(title='Correlation')))
fig11.update_layout(title='Dynamic Cross-Correlation Matrix', xaxis_title='Residue index', yaxis_title='Residue index', width=750, height=750)
fig11.data[0].hovertext = [[f'Residue i: {i+1}<br>Residue j: {j+1}<br>Correlation: {dccm[i,j]:.2f}' for j in range(dccm.shape[1])] for i in range(dccm.shape[0])]
fig11.data[0].hoverinfo = 'text'
fig11.show()

**사용된 패키지들**

*  OpenMM
> P. Eastman, J. Swails, J. D. Chodera, R. T. McGibbon, Y. Zhao, K. A. Beauchamp, L.-P. Wang, A. C. Simmonett, M. P. Harrigan, C. D. Stern, R. P. Wiewiora, B. R. Brooks, and V. S. Pande. (2017) "OpenMM 7: Rapid development of high performance algorithms for molecular dynamics.” PLOS Comp. Biol. 13(7): e1005659. DOI:[10.1371/journal.pcbi.1005659](https://doi.org/10.1371/journal.pcbi.1005659)

* PDB2PQR
> T. J. Dolinsky, J. E. Nielsen, J. A. McCammon, and N. A. Baker. (2004) "PDB2PQR: an automated pipeline for the setup, execution, and analysis of Poisson-Boltzmann electrostatics calculations." Nucleic Acids Res. 32: W665-667. DOI:[10.1093/nar/gkh381](https://doi.org/10.1093/nar/gkh381)

* PropKa
> H. Li, A. D. Robertson, and J. H. Jensen. (2005) "Very Fast Empirical Prediction and Rationalization of Protein pKa Values." Proteins, 61: 704-721. DOI:[10.1002/prot.20660](https://doi.org/10.1002/prot.20660)

*  NGLViewer
> H. Nguyen, D. A. Case, and A. S. Rose. (2018) "NGLview - Interactive molecular graphics for Jupyter notebooks" Bioinformatics 34(7): 1241-1242. DOI:[10.1093/bioinformatics/btx789](https://doi.org/10.1093/bioinformatics/btx789)

* MDTraj
> R. T. McGibbon, K. A. Beauchamp, M. P. Harrigan, C. Klein, J. M. Swails, C. X. Hernández, C. R. Schwantes, L-P. Wang, T. J. Lane, and V. S. Pande (2011) "MDTraj: A Modern Open Library for the Analysis of Molecular Dynamics Trajectories" Biophys. J. 109(8): 1528-1532. DOI:[10.1016/j.bpj.2015.08.015](https://doi.org/10.1016/j.bpj.2015.08.015)

* NumPy
> C. R. Harris, K. J. Millman, S. J. van der Walt et al. (2020) "Array programming with NumPy" Nature 585, 357-362. DOI:[10.1038/s41586-020-2649-2](https://doi.org/10.1038/s41586-020-2649-2)

* Scikit-learn
> F. Pedregosa, G. Varoquaux, A. Gramfort, V. Michel, B. Thirion, O. Grisel, M. Blondel, P. Prettenhofer, R. Weiss, V. Dubourg, J. Vanderplas, A. Passos, David Cournapeau, M. Brucher, M. Perrot, and E. Duchesnay (2011) "Scikit-learn: Machine Learning in Python" JMLR 12(85): 2825-2830. (https://jmlr.csail.mit.edu/papers/v12/pedregosa11a.html)

* Plotly
> Plotly Technologies Inc. (https://plot.ly)

* ipywidgets
> Jupyter widgets community (https://github.com/jupyter-widgets/ipywidgets)

